# Strategia Regressione

<b><font color=RED size=+2>We predict returns and not prices!</font></b>

In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
plt.style.use("seaborn")
from sklearn.linear_model import LinearRegression

In [ ]:
# WITH OANDA
import tpqoa
api = tpqoa.tpqoa("oandaMY.cfg")

In [ ]:
# WITH IBKR
# ib.disconnect()
import pandas as pd
from ib_insync import *
util.startLoop()  # not necessary in scripts
ib = IB()
ib.connect()

In [ ]:
# WITH OANDA
df = api.get_history(instrument = "EUR_USD", start = "2024-08-24", end = "2024-09-24", granularity = "M5", price = "M")
# we change the column names to match IBKR
df.rename(columns={"o":"open","h":"high","l":"low","c":"close","time":"date"},inplace=True)
df.index.names = ['date']
df = df.close.to_frame()
df.head(5)

In [ ]:
# WITH IBKR
df = pd.DataFrame(ib.reqHistoricalData( Forex("EURUSD"), endDateTime = "20240924 00:00:00", 
                                  barSizeSetting="5 mins", durationStr="1 M", 
                                  whatToShow= "MIDPOINT", useRTH = True, formatDate=2 )).set_index("date")
df.index=pd.to_datetime(df.index)
df = df.close.to_frame()
df.head(5)

In [ ]:
df.info()

In [ ]:
df.plot()

In [ ]:
df.loc["2023-10-20":"2023-10-27"].plot()

In [ ]:
from sklearn.linear_model import LinearRegression

# Regressione multilineare

In [ ]:
df = api.get_history(instrument="EUR_USD", start="2023-01-01", 
                     end="2023-10-29" , granularity = "M5", price = "M")["c"].to_frame().dropna()

In [ ]:
df2 = api.get_history(instrument="EUR_USD", start="2023-01-01", 
                     end="2023-10-29" , granularity = "H3", price = "M")["c"].to_frame().dropna()
df2["logRet"]=np.log(df2.c/df2.c.shift(1))
lags=5
colonne=[]
for lag in range(1,lags+1):
    col = "logRet"+str(lag)
    df2[col]=df2.logRet.shift(lag)
    colonne.append(col)
df2.dropna(inplace=True)
lm = LinearRegression(fit_intercept=True)
lm.fit(X=df2[colonne],y=df2.logRet)
df2["predicted"]=np.sign(lm.predict(df2[colonne]))
df2["transazioni"]= abs(df2.predicted-df2.predicted.shift(1))

In [ ]:
(df2.predicted*df2.logRet-df2.transazioni*(comm+spread/2)).cumsum().plot()

# Forward testing

In [ ]:
# ATTENZIONE che lo addestriamo sui dati dell'anno precedente
train = api.get_history(instrument="EUR_USD", start="2022-01-01", 
                     end="2022-10-29" , granularity = "H3", price = "M")["c"].to_frame().dropna()
train["logRet"]=np.log(train.c/train.c.shift(1))
lags=5
colonne=[]
for lag in range(1,lags+1):
    col = "logRet"+str(lag)
    train[col]=train.logRet.shift(lag)
    colonne.append(col)
train.dropna(inplace=True)
lm2022 = LinearRegression(fit_intercept=True)
lm2022.fit(X=train[colonne],y=train.logRet)